In [ ]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plot
from scipy import stats


from sklearn import linear_model
from sklearn.metrics import r2_score

from statsmodels.compat import lzip
import statsmodels.api as sm
import statsmodels.stats.api as sms
import statsmodels.formula.api as smf
from statsmodels.sandbox.regression.predstd import wls_prediction_std

np.random.seed(9876789)

Read the csv file


In [ ]:
data = pd.read_csv('mtcars.csv', sep=",")
data.shape


In [ ]:
data.head()


In [ ]:
plot.scatter(data['wt'], data['mpg'])
plot.xlabel('Weight', fontsize=18)
plot.ylabel('Miles per gallon', fontsize=16)


## Fit linear model with weight using **sklearn**:
 
mpg = a + b weight + error

y  =  a + b x + error


In [ ]:
x = data[["wt"]]
y = data[["mpg"]]

lm = linear_model.LinearRegression()

fit_m1 = lm.fit(X=x,y=y)

In [ ]:
intercept = fit_m1.intercept_
print('a = ',intercept)

beta = fit_m1.coef_
print('b = ',beta)


In [ ]:
y_hat = intercept + np.dot(x,beta)


a = 37.285 and b = -5.344

In [ ]:
def abline(slope, intercept):
    """Plot a line from slope and intercept"""
    axes = plot.gca()
    x_vals = np.array(axes.get_xlim())
    y_vals = intercept + slope * x_vals
    plot.plot(x_vals, y_vals, '--')
plot.scatter(data['wt'], data['mpg'])
plot.xlabel('Weight', fontsize=18)
plot.ylabel('Miles per gallon', fontsize=16)
abline(slope=-5.344,intercept=37.285)


### Model evaluation


In [ ]:
R2 = r2_score(y,y_hat)  
print(round(R2,3))

In [ ]:
plot.scatter(y,y_hat)
plot.xlabel('MPG', fontsize=18)
plot.ylabel('MPG Predicted', fontsize=16)


## Fit linear model with weight using **statmodels**:


In [ ]:
model = sm.OLS(y, x)
results = model.fit()
print(results.summary())

## Fit linear model with wt and hp using **sklearn**:

In [ ]:
x = data[["wt", "hp"]]
y = data[["mpg"]]


In [ ]:
fit_m2 = lm.fit(X=x,y=y)

intercept = fit_m2.intercept_

## Prepare a new data for prototype car with 

wt = 3 
hp   = 120 


In [ ]:
x_new = np.array([[3, 120]])
beta = fit_m2.coef_
beta.shape
beta = np.transpose(beta)
beta.shape


In [ ]:
pred = intercept + np.dot(x_new,beta)
pred

### Calculate Total Sum of Squares of Error


In [ ]:
y_hat = intercept + np.dot(x,beta)

error_sqr = np.square(y-y_hat)


### Calculate Total Sum of Squares of Error 

In [ ]:
TSS = np.sum(error_sqr)

n = x.shape[0]
p = x.shape[1]


### Mean sum of squares

In [ ]:
MSS = TSS/(n-p-1)


### Residual standard error 

In [ ]:
Residual_standard_error = np.sqrt(MSS)
print('Residual Standard Error = ',Residual_standard_error)


## Confidence Interval

$$
mpg \sim N(\beta_0+\beta_1 wt + \beta_2 hp , \sigma^2)
$$

Residual standard error (= $s^2$) is an unbiased estimator of $\sigma^2$.

In [ ]:
lower_bound = pred - [[1.96*Residual_standard_error]]
upper_bound = pred + [[1.96*Residual_standard_error]]

print('lower bound = ',lower_bound, 'upper bound = ', upper_bound)

### Model evaluation


In [ ]:
R2 = r2_score(y,y_hat) 

print(R2)

plot.scatter(y,y_hat)
plot.xlabel('MPG', fontsize=18)
plot.ylabel('MPG Predicted', fontsize=16)



### Let's explore the relationship between hp and mpg


In [ ]:
plot.scatter(data['hp'], data['mpg'])
plot.xlabel('Horse Power', fontsize=18)
plot.ylabel('Miles per gallon', fontsize=16)


### Variable transformation or feature engineering.


In [ ]:
x['hp2'] = x['hp']**2

In [ ]:
x.head()


In [ ]:
fit_m3 = lm.fit(X=x,y=y)

y_hat = fit_m3.predict(X=x)


### Model evaluation


In [ ]:
R2 = r2_score(y,y_hat)  
print(R2)

plot.scatter(y,y_hat)
plot.xlabel('MPG', fontsize=18)
plot.ylabel('MPG Predicted', fontsize=16)



In [ ]:
model = sm.OLS(y, x)
results = model.fit()
print(results.summary())

In [ ]:
data['hp2'] = data['hp']**2
data.head()

In [ ]:
results = smf.ols('mpg ~ wt + hp + hp2', data=data).fit()
print(results.summary())

## Check Model Assumptions:

In [ ]:
resid = y - y_hat

plot.scatter(y_hat,resid)
plot.xlabel('MPG Predicted', fontsize=18)
plot.ylabel('Residual', fontsize=16)


## Breush-Pagan test for Homoscadaticity

In [ ]:
name = ['Lagrange multiplier statistic', 'p-value',
        'f-value', 'f p-value']
BPtest = sms.het_breuschpagan(results.resid, results.model.exog)
BPtest = np.round(BPtest,5)
lzip(name, BPtest)

In [ ]:
resid = results.resid
resid.hist(bins = 20)
plot.xlabel('Residual', fontsize=18)
plot.ylabel('Frequency',fontsize=15)
plot.title('Histogram of Residuals')
plot.show()

## Kolmogorov-Smironov Test for Normality

In [ ]:
resid = results.resid
stats.kstest(resid, 'norm')
